## Livability Mapping

In this notebook, we map the livability of different regions based on spatial data, using a shapefile that contains geographic boundaries for Statistical Areas Level 2 (SA2) in Australia. This allows us to analyze how livability varies across different regions.




In [1]:
import pandas as pd
import geopandas as gpd


In [2]:
sf2 = gpd.read_file("/root/MAST30034_Python/data/vic_zones/SA2_2021_AUST_GDA2020.shp")
sf2.head()

SA2_CODE21                       SA2_NAME21 CHG_FLAG21  CHG_LBL21  \
0  101021007                        Braidwood          0  No change   
1  101021008                          Karabar          0  No change   
2  101021009                       Queanbeyan          0  No change   
3  101021010                Queanbeyan - East          0  No change   
4  101021012  Queanbeyan West - Jerrabomberra          0  No change   

  SA3_CODE21  SA3_NAME21 SA4_CODE21      SA4_NAME21 GCC_CODE21   GCC_NAME21  \
0      10102  Queanbeyan        101  Capital Region      1RNSW  Rest of NSW   
1      10102  Queanbeyan        101  Capital Region      1RNSW  Rest of NSW   
2      10102  Queanbeyan        101  Capital Region      1RNSW  Rest of NSW   
3      10102  Queanbeyan        101  Capital Region      1RNSW  Rest of NSW   
4      10102  Queanbeyan        101  Capital Region      1RNSW  Rest of NSW   

  STE_CODE21       STE_NAME21 AUS_CODE21 AUS_NAME21  AREASQKM21  \
0          1  New South Wales        AUS  Australia   3418.3525   
1          1  New South Wales        AUS  Australia      6.9825   
2          1  New South Wales        AUS  Australia      4.7620   
3          1  New South Wales        AUS  Australia     13.0032   
4          1  New South Wales        AUS  Australia     13.6748   

                                          LOCI_URI21  \
0  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
1  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
2  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
3  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
4  http://linked.data.gov.au/dataset/asgsed3/SA2/...   

                                            geometry  
0  POLYGON ((149.58424 -35.44426, 149.58444 -35.4...  
1  POLYGON ((149.21899 -35.36738, 149.218 -35.366...  
2  POLYGON ((149.21326 -35.34325, 149.21619 -35.3...  
3  POLYGON ((149.24034 -35.34781, 149.24024 -35.3...  
4  POLYGON ((149.19572 -35.36126, 149.1997 -35.35...

In [3]:
# Set the 'Suburb' column as the index
sf2.set_index('SA2_NAME21', inplace=True)

In [4]:
rent_data_cleaned = pd.read_csv("/root/project-2-group-real-estate-industry-project-34/data/landing/sa2_growth_filtered.csv")


In [8]:
# Convert 'SA2_CODE21' to string type
rent_data_cleaned['SA2_CODE21'] = rent_data_cleaned['SA2_CODE21'].astype(str)
# Convert 'SA2_CODE21' to string type
sf2['SA2_CODE21'] = sf2['SA2_CODE21'].astype(str)


In [15]:
proportions = rent_data_cleaned[["SA2_CODE21","predicted_price_2027"]] 

In [11]:
gdf = gpd.GeoDataFrame(
    pd.merge(proportions, sf2, on='SA2_CODE21', how='inner')
)

gdf.head()

SA2_CODE21  predicted_price_2027 CHG_FLAG21  CHG_LBL21 SA3_CODE21  \
0  212041563            519.777750          1        New      21204   
1  210051445            496.114806          0  No change      21005   
2  209041528            526.170944          1        New      20904   
3  207031163            562.160111          0  No change      20703   
4  206041506            718.729556          1        New      20604   

                   SA3_NAME21 SA4_CODE21              SA4_NAME21 GCC_CODE21  \
0                   Dandenong        212  Melbourne - South East      2GMEL   
1  Tullamarine - Broadmeadows        210  Melbourne - North West      2GMEL   
2         Whittlesea - Wallan        209  Melbourne - North East      2GMEL   
3           Whitehorse - West        207  Melbourne - Inner East      2GMEL   
4              Melbourne City        206       Melbourne - Inner      2GMEL   

          GCC_NAME21 STE_CODE21 STE_NAME21 AUS_CODE21 AUS_NAME21  AREASQKM21  \
0  Greater Melbourne          2   Victoria        AUS  Australia      8.0410   
1  Greater Melbourne          2   Victoria        AUS  Australia     70.8359   
2  Greater Melbourne          2   Victoria        AUS  Australia      5.0223   
3  Greater Melbourne          2   Victoria        AUS  Australia      7.0123   
4  Greater Melbourne          2   Victoria        AUS  Australia      2.4248   

                                          LOCI_URI21  \
0  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
1  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
2  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
3  http://linked.data.gov.au/dataset/asgsed3/SA2/...   
4  http://linked.data.gov.au/dataset/asgsed3/SA2/...   

                                            geometry  
0  POLYGON ((145.1938 -37.97428, 145.19408 -37.97...  
1  POLYGON ((144.97609 -37.52848, 144.97609 -37.5...  
2  POLYGON ((145.10426 -37.60955, 145.10425 -37.6...  
3  POLYGON ((145.11504 -37.81688, 145.11518 -37.8...  
4  POLYGON ((144.93585 -37.79507, 144.93569 -37.7...

In [12]:
geoJSON = gdf[['SA2_CODE21', 'geometry']].drop_duplicates('SA2_CODE21').to_json()

In [13]:
import folium

In [22]:
# Perform the inner join on 'Place of Usual Residence' from df and 'Code' from forecasted_df
proportions = pd.merge(proportions, gdf[['SA2_CODE21', 'geometry']],
                     left_on='SA2_CODE21', right_on='SA2_CODE21', how='inner')

## Geospatial Mapping of Predicted Property Prices

In this section, we visualize the predicted property prices for the year 2027 across different SA2 regions using a **Choropleth map**. The map provides a color-coded representation of the predicted prices, making it easier to see spatial patterns in the data.

### Steps Involved:

1. **Define a Color Scale**:
   We created a custom scale (`myscale`) to define the thresholds for coloring the regions based on the predicted property prices. The scale is set with 10 bins ranging from 450 to 800, representing different price ranges.

   ```python
   myscale = [450, 500, 550, 600, 650, 700, 750, 800]


In [20]:
myscale = [450, 500, 550, 600, 650, 700, 750, 800]

# Plot the map with 10 bins
m = folium.Map(location=[-37.83467, 144.97445], zoom_start=10)
c = folium.Choropleth(
 geo_data=geoJSON,
 name='Choropleth',
 data=proportions,
 columns=['SA2_CODE21', 'predicted_price_2027'],
 key_on="properties.SA2_CODE21",
 fill_color='YlGnBu',
 threshold_scale=myscale,
 fill_opacity=1,
 line_opacity=0.2,
 legend_name='Predicted property prices',
 smooth_factor=0
)
c.add_to(m)


m

In [21]:
m.save("predicted_prices.html")